<img src="images/oasis-lmf-colour.png" alt="Oasis LMF logo" width="250" align="left"/>
<br><br><br>

# Excercise 2:   Introduction to Oasis model files and formats.

The Oasis kernel provides a robust loss simulation engine for catastrophe modelling. Insurance practitioners are used to dealing with losses arising from events. These losses are numbers, not distributions. Policy terms are applied to the losses individually and then aggregated and further conditions or reinsurances applied. Oasis takes the same perspective, which is to generate individual losses from the probability distributions. The way to achieve this is random sampling called “Monte-Carlo” sampling from the use of random numbers, as if from a roulette wheel, to solve equations that are otherwise intractable.

Modelled and empirical intensities and damage responses can show significant uncertainty, Sometimes this uncertainty is multi-modal, meaning that there can be different peaks of behaviour rather than just a single central behaviour. Moreover, the definition of the source insured interest characteristics, such as location or occupancy or construction, can be imprecise. The associated values for event intensities and consequential damages can therefore be varied and their uncertainty can be represented in general as probability distributions rather than point values. The design of Oasis therefore makes no assumptions about the probability distributions and instead treats all probability distributions as probability masses in discrete bins. This includes closed interval point bins such as the values [0,0] for no damage and [1,1] for total damage.

The simulation approach taken by the Oasis calculation kernel computes a single cumulative distribution function (CDF) for the damage by “convolving” the binned intensity distribution with the vulnerability matrices. Sampling can then be done against the CDF. 

<img src="images/simulation_methodology.png" alt="Oasis simulation methodology" width="600"/>

The Oasis kernel requires a standard set of files for capturing the hazard footprints and vulnerability data.

<img src="images/oasis_model_files.png" alt="Oasis model files" width="600"/>

The files are:

#### area peril dictionary
    The meta-data that describes the model specific geo-spatial grid. This can be a set of points, a regular grid or a variable resolutiuon grid.
#### intensity bin dictionary
    The meta-data that descibes the hazard intensities corresponding to the bins.
#### hazard
    The hazard values for each impacted area peril cell for each event in the stochastic catalogue.
#### damage bin dictionary
    The meta-data tha descibes the damage percentages corresponding to the bins.
#### vulnerability dictionary
    The meta-data that descibes the vulnerability data, in particular mapping particular curves to particular exposure attributes.
#### vulnerability
    The vulnerability data. 
#### event
    The list of events in the stochastic catalogue. Event files can be use to distinguish event types, such as historical.
#### occurrences
    The list of event occurrences in particular periods, used for loss curve calculations.

## Example model
For the excercises, we are using a cut-down version of the Catrisks' Middle East Earthquake model. We include the full catalogue of events, but only for an area around the city of Beirut. The intensity bins dictionary only includes "hazard levels" and not actual PGA values, protecting the Catrisk IP in the example. The intensity levels are not required for loss calculations, which only depend on the event hazard getting linked to the correct damage level. This model contains both hazard and damage uncertainty.


## Excercise goals
* Understand the Oasis model files
* Use Python code to view the model files for an example model
* Use Python code to visualise run and view the results of an analysis


In [ ]:
%config IPCompleter.greedy=True

In [51]:
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import geopandas as gpd
import math
import numpy as np
import json
import seaborn as sns
import folium
import os
from shapely.geometry import Point, Polygon
from numpy import linspace
from bokeh import events
from bokeh.io import output_file, show, output_notebook
from bokeh.models import ColumnDataSource, FixedTicker, PrintfTickFormatter, CustomJS, Div, TapTool
from bokeh.plotting import figure
import branca.colormap as cm
import datetime

# Output Bokeh charts to notebook, rather than opening a browser window
output_notebook()

map_centre = [18.64, -70.09]
map_zoom = 8

Loading BokehJS ...

## View the model files

### Area peril dictionary

In [42]:
area_peril_dictionary = pd.read_csv("./gem/keys_data/GMO/areaperil_dict.csv")
area_peril_dictionary.columns = [x.lower() for x in area_peril_dictionary.columns]
area_peril_dictionary.head()

areaperil_id       lon        lat       xmin       xmax       ymin  \
0         12225 -72.07917  18.554171 -72.095833 -72.062500  18.537500   
1         12226 -72.07917  18.587500 -72.095833 -72.062500  18.570833   
2         12227 -72.07917  18.620831 -72.095833 -72.062500  18.604167   
3         12228 -72.07917  18.654169 -72.095833 -72.062500  18.637500   
4         12229 -72.04583  18.520830 -72.062500 -72.029167  18.504167   

        ymax  
0  18.570833  
1  18.604167  
2  18.637500  
3  18.670833  
4  18.537500

In [52]:
m = folium.Map(tiles='cartodbpositron', location=map_centre, zoom_start=map_zoom)
for i, row in area_peril_dictionary.iterrows():
    folium.CircleMarker(
        location=[row.lat, row.lon], radius=1).add_to(m)
m

### Intensity bin dictionary

In [53]:
intensity_bin_dictionary = pd.read_csv("./gem/model_data/GMO/intensity_bin_dict.csv")
area_peril_dictionary.columns = [x.lower() for x in area_peril_dictionary.columns]
intensity_bin_dictionary.head()

bin_index  bin_from  bin_to  interpolation  interval_type type
0        210      0.00    0.05         0.0001           1201  PGA
1        211      0.05    0.10         0.0750           1201  PGA
2        212      0.10    0.15         0.1250           1201  PGA
3        213      0.15    0.20         0.1750           1201  PGA
4        214      0.20    0.25         0.2250           1201  PGA

### Hazard

In [54]:
footprints = pd.read_csv("./gem/model_data/GMO/footprint_pga.csv")
footprints.head()

event_id  areaperil_id  intensity_bin_index      prob
0         1         12283                  210  0.961852
1         1         12283                  211  0.038148
2         1         12397                  210  0.962974
3         1         12397                  211  0.037026
4         1         12400                  210  0.961852

In [55]:
event_id = 2401
area_peril_id = 15939

In [56]:
footprints_with_hazard = footprints.merge(
    area_peril_dictionary, how='inner', 
    on='areaperil_id').merge(
    intensity_bin_dictionary, how="inner",
    left_on="intensity_bin_index", right_on="bin_index")
footprint_with_hazard = footprints_with_hazard[footprints_with_hazard.event_id == event_id]
footprint_with_hazard = footprint_with_hazard[['areaperil_id', 'lat', 'lon', 'prob', 'intensity_bin_index','interpolation']] 
footprint_with_hazard = footprint_with_hazard.sort_values(['areaperil_id'])
footprint_with_hazard = footprint_with_hazard.rename(index=str, columns={"interpolation": "hazard"})
footprint_with_hazard
#footprint_with_hazard.head()

areaperil_id        lat        lon      prob  intensity_bin_index  \
446887           12225  18.554171 -72.079170  0.890011                  210   
6692595          12225  18.554171 -72.079170  0.074052                  211   
12813179         12225  18.554171 -72.079170  0.035937                  212   
6693409          12226  18.587500 -72.079170  0.111078                  211   
447670           12226  18.587500 -72.079170  0.888922                  210   
11384768         12227  18.620831 -72.079170  0.110022                  211   
5057523          12227  18.620831 -72.079170  0.889978                  210   
11319195         12228  18.654169 -72.079170  0.111111                  211   
4991811          12228  18.654169 -72.079170  0.888889                  210   
7143196          12229  18.520830 -72.045830  0.220011                  211   
889835           12229  18.520830 -72.045830  0.779989                  210   
11385581         12230  18.554171 -72.045830  0.071874                  211   
5058313          12230  18.554171 -72.045830  0.928126                  210   
7143875          12231  18.587500 -72.045830  0.035937                  211   
890495           12231  18.587500 -72.045830  0.964063                  210   
11386265         12232  18.620831 -72.045830  0.188496                  211   
5058987          12232  18.620831 -72.045830  0.737452                  210   
18785798         12232  18.620831 -72.045830  0.074052                  213   
5396545          12233  18.654169 -72.045830  0.924826                  210   
11728750         12233  18.654169 -72.045830  0.075174                  211   
11386952         12234  18.687500 -72.045830  0.075174                  211   
5059655          12234  18.687500 -72.045830  0.924826                  210   
5060221          12235  18.487499 -72.012497  0.773289                  210   
18786079         12235  18.487499 -72.012497  0.038148                  213   
11387537         12235  18.487499 -72.012497  0.151537                  211   
15265110         12235  18.487499 -72.012497  0.037026                  212   
11388097         12236  18.520830 -72.012497  0.111111                  211   
5060769          12236  18.520830 -72.012497  0.888889                  210   
5061434          12237  18.554171 -72.012497  0.891100                  210   
11388785         12237  18.554171 -72.012497  0.108900                  211   
...                ...        ...        ...       ...                  ...   
15230778         18326  18.720831 -68.345833  0.108900                  212   
4976930          18326  18.720831 -68.345833  0.482626                  210   
11305248         18327  18.754169 -68.345833  0.075174                  211   
4977926          18327  18.754169 -68.345833  0.924826                  210   
17200957         18328  18.454170 -68.312500  0.037026                  213   
12645235         18328  18.454170 -68.312500  0.072963                  212   
113307           18328  18.454170 -68.312500  0.629674                  210   
6355580          18328  18.454170 -68.312500  0.260337                  211   
889075           18329  18.487499 -68.312500  0.778900                  210   
7142429          18329  18.487499 -68.312500  0.221100                  211   
6592750          18330  18.520830 -68.312500  0.224400                  211   
12760127         18330  18.520830 -68.312500  0.072963                  212   
348901           18330  18.520830 -68.312500  0.702637                  210   
4978915          18331  18.554171 -68.312500  0.668911                  210   
20559789         18331  18.554171 -68.312500  0.037026                  216   
11306240         18331  18.554171 -68.312500  0.182952                  211   
15231808         18331  18.554171 -68.312500  0.072963                  212   
18768308         18331  18.554171 -68.312500  0.038148                  213   
349802           18332  18.587500 -68.312500  0.591459      

In [64]:
footprint_with_hazard_for_cell = footprint_with_hazard[footprint_with_hazard.areaperil_id == area_peril_id] 
footprint_with_hazard_for_cell = intensity_bin_dictionary.merge(
    footprint_with_hazard_for_cell, how="inner",
    left_on="bin_index", right_on="intensity_bin_index", suffixes=('', '_dict'))

footprint_with_hazard_for_cell.fillna(0)
footprint_with_hazard_for_cell = footprint_with_hazard_for_cell.sort_values("intensity_bin_index")
footprint_with_hazard_for_cell = footprint_with_hazard_for_cell[['prob', 'intensity_bin_index','interpolation']]
footprint_with_hazard_for_cell = footprint_with_hazard_for_cell.rename(index=str, columns={"interpolation": "hazard"})
footprint_with_hazard_for_cell
#footprint_with_hazard_for_cell.head()

prob  intensity_bin_index  hazard
0   0.037026                  213   0.175
1   0.037026                  214   0.225
2   0.038148                  215   0.275
3   0.072963                  216   0.325
4   0.072963                  217   0.375
5   0.038148                  218   0.425
6   0.111078                  219   0.475
7   0.112200                  220   0.525
8   0.038148                  221   0.575
9   0.035937                  222   0.625
10  0.144837                  223   0.675
11  0.037026                  224   0.725
12  0.038148                  225   0.775
13  0.077452                  226   0.825
14  0.072963                  231   1.075
15  0.035937                  233   1.175

In [59]:
footprint_with_hazard['weighted_hazard'] = footprint_with_hazard['hazard'] * footprint_with_hazard['prob'] 
footprint_with_mean_hazard = pd.DataFrame({'mean_hazard' : footprint_with_hazard.groupby( ['areaperil_id', 'lat', 'lon'] )['weighted_hazard'].sum()}).reset_index()

linear = cm.LinearColormap(
    ['green', 'yellow', 'red'],
    vmin=min(footprint_with_mean_hazard.mean_hazard), 
    vmax=max(footprint_with_mean_hazard.mean_hazard))
m = folium.Map(location=map_centre, zoom_start=map_zoom, tiles='cartodbpositron')
for i, row in footprint_with_mean_hazard.iterrows():
    c = linear(row.mean_hazard)
    folium.CircleMarker(
        location=[row.lat, row.lon], fill_color=c, radius=5,
        weight=0, fill=True, fill_opacity=1.0).add_to(m)
linear.caption = 'Hazard'
m.add_child(linear)
m.fit_bounds(m.get_bounds())
m

In [66]:
intensity_range = (0, footprint_with_hazard_for_cell.hazard.max())
p = figure(x_range=intensity_range, plot_height=300, y_range=(0, footprint_with_hazard_for_cell.prob.max()), toolbar_location=None)
p.vbar(x=footprint_with_hazard_for_cell.hazard, top=footprint_with_hazard_for_cell.prob, width=0.9)
p.xaxis.axis_label = 'Hazard'
p.yaxis.axis_label = 'Probability'
show(p)

### Damage bin dictionary

In [68]:
damage_bin_dictionary = pd.read_csv("./gem/model_data/GMO/damage_bin_dict.csv")
damage_bin_dictionary

bin_index  bin_from    bin_to  interpolation  interval_type
0            1  0.000000  0.000000       0.000000           1201
1            2  0.000001  0.000002       0.000002           1201
2            3  0.000002  0.000003       0.000003           1201
3            4  0.000003  0.000004       0.000004           1201
4            5  0.000004  0.000005       0.000005           1201
5            6  0.000005  0.000006       0.000005           1201
6            7  0.000006  0.000007       0.000007           1201
7            8  0.000007  0.000008       0.000007           1201
8            9  0.000008  0.000009       0.000008           1201
9           10  0.000009  0.000011       0.000010           1201
10          11  0.000011  0.000012       0.000012           1201
11          12  0.000012  0.000014       0.000013           1201
12          13  0.000014  0.000016       0.000015           1201
13          14  0.000016  0.000019       0.000017           1201
14          15  0.000019  0.000022       0.000021           1201
15          16  0.000022  0.000025       0.000023           1201
16          17  0.000025  0.000028       0.000027           1201
17          18  0.000028  0.000033       0.000030           1201
18          19  0.000033  0.000038       0.000035           1201
19          20  0.000038  0.000043       0.000041           1201
20          21  0.000043  0.000050       0.000047           1201
21          22  0.000050  0.000057       0.000054           1201
22          23  0.000057  0.000066       0.000062           1201
23          24  0.000066  0.000076       0.000071           1201
24          25  0.000076  0.000087       0.000081           1201
25          26  0.000087  0.000100       0.000094           1201
26          27  0.000100  0.000115       0.000107           1201
27          28  0.000115  0.000132       0.000124           1201
28          29  0.000132  0.000152       0.000142           1201
29          30  0.000152  0.000175       0.000163           1201
..         ...       ...       ...            ...            ...
136        137  0.700000  0.710000       0.705000           1201
137        138  0.710000  0.720000       0.715000           1201
138        139  0.720000  0.730000       0.725000           1201
139        140  0.730000  0.740000       0.735000           1201
140        141  0.740000  0.750000       0.745000           1201
141        142  0.750000  0.760000       0.755000           1201
142        143  0.760000  0.770000       0.765000           1201
143        144  0.770000  0.780000       0.775000           1201
144        145  0.780000  0.790000       0.785000           1201
145        146  0.790000  0.800000       0.795000           1201
146        147  0.800000  0.810000       0.805000           1201
147        148  0.810000  0.820000       0.815000           1201
148        149  0.820000  0.830000       0.825000           1201
149        150  0.830000  0.840000       0.835000           1201
150        151  0.840000  0.850000       0.845000           1201
151        152  0.850000  0.860000       0.855000           1201
152        153  0.860000  0.870000       0.865000           1201
153        154  0.870000  0.880000       0.875000           1201
154        155  0.880000  0.890000       0.885000           1201
155        156  0.890000  0.900000       0.895000           1201
156        157  0.900000  0.910000       0.905000           1201
157        158  0.910000  0.920000       0.915000           1201
158        159  0.920000  0.930000       0.925000           1201
159        160  0.930000  0.940000       0.935000           1201
160        161  0.940000  0.950000       0.945000           1201
161        162  0.950000  0.960000       0.955000           1201
162        163  0.960000  0.970000       0.965000           1201
163        164  0.970000  0.980000       0.975000           1201
164        165  0.980000  0.990000       0.985000           1201
165        166  0.990000  1.000000      

### Vulnerability dictionary

In [70]:
vulnerability_dict = pd.read_csv("./gem/keys_data/GMO/vulnerability_dict.csv")
vulnerability_dict

vulnerability_id               taxonomy     type  imtMin   imtMax  \
0                  1       CR_LDUAL-DUH_H12  SA(0.6)    0.05  5.19640   
1                  2    CR_LDUAL-DUH_H12-24  SA(0.6)    0.05  5.19640   
2                  3        CR_LDUAL-DUH_H7  SA(0.3)    0.05  5.22239   
3                  4        CR_LFINF-DNO_H2      PGA    0.05  5.19615   
4                  5        CR_LFINF-DNO_H3  SA(0.3)    0.05  5.22239   
5                  6        CR_LFINF-DNO_H4  SA(0.3)    0.05  5.22239   
6                  7        CR_LFINF-DNO_H5  SA(0.3)    0.05  5.22239   
7                  8        CR_LFINF-DUH_H2      PGA    0.05  5.19615   
8                  9        CR_LFINF-DUH_H3  SA(0.3)    0.05  5.22239   
9                 10        CR_LFINF-DUH_H4  SA(0.3)    0.05  5.22239   
10                11        CR_LFINF-DUH_H5  SA(0.3)    0.05  5.22239   
11                12        CR_LFINF-DUH_H6  SA(0.3)    0.05  5.22239   
12                13          CR_LFM-DNO_H1      PGA    0.05  5.19615   
13                14          CR_LFM-DNO_H2      PGA    0.05  5.19615   
14                15        MCF_LWAL-DNO_H1      PGA    0.05  5.19615   
15                16        MCF_LWAL-DNO_H2      PGA    0.05  5.19615   
16                17        MCF_LWAL-DNO_H3  SA(0.3)    0.05  5.22239   
17                18        MCF_LWAL-DUH_H1      PGA    0.05  5.19615   
18                19        MCF_LWAL-DUH_H2      PGA    0.05  5.19615   
19                20        MCF_LWAL-DUH_H3  SA(0.3)    0.05  5.22239   
20                21         MR_LWAL-DNO_H1      PGA    0.05  5.19615   
21                22         MR_LWAL-DNO_H2      PGA    0.05  5.19615   
22                23         MR_LWAL-DNO_H3  SA(0.3)    0.05  5.22239   
23                24         MR_LWAL-DUH_H1      PGA    0.05  5.19615   
24                25         MR_LWAL-DUH_H2      PGA    0.05  5.19615   
25                26         MR_LWAL-DUH_H3  SA(0.3)    0.05  5.22239   
26                27        MUR_LWAL-DNO_H1      PGA    0.05  5.19615   
27                28        MUR_LWAL-DNO_H2  SA(0.3)    0.05  5.22239   
28                29                 UNK_H1      PGA    0.05  5.19615   
29                30       W-WBB_LPB-DNO_H1  SA(0.3)    0.05  3.01009   
30                31      W-WLI_LWAL-DNO_H1  SA(0.3)    0.05  3.01009   
31                32      W-WLI_LWAL-DNO_H2  SA(0.3)    0.05  3.01009   
32                33  W-WLI_LWAL-DNO_H2_SOS  SA(0.3)    0.05  3.01009   
33                34        W-WS_LPB-DNO_H1  SA(0.3)    0.05  3.01009   
34                35      W-WWD_LWAL-DNO_H1      PGA    0.05  5.19615   
35                36      CR-PC_LWAL-DNO_H1  SA(0.3)    0.05  3.01009   
36                37        CR_LFINF-DUM_H2  SA(0.3)    0.05  3.01009   
37                38        CR_LFINF-DUM_H3  SA(0.3)    0.05  3.01009   
38                39        CR_LFINF-DUM_H4  SA(0.6)    0.05  3.00009   
39                40        CR_LFINF-DUM_H5  SA(0.6)    0.05  3.00009   
40                41        CR_LFINF-DUM_H6  SA(1.0)    0.05  3.00009   
41                42        MCF_LWAL-DUM_H1      PGA    0.05  3.00000   
42                43        MCF_LWAL-DUM_H2  SA(0.3)    0.05  3.01009   
43                44        MCF_LWAL-DUM_H3  SA(0.3)    0.05  3.01009   
44                45         MR_LWAL-DUM_H1  SA(0.3)    0.05  3.01009   
45                46         MR_LWAL-DUM_H2  SA(0.3)    0.05  3.01009   
46                47         MR_LWAL-DUM_H3  SA(0.3)    0.05  3.01009   
47                48    MUR-ADO_LWAL-DNO_H1      PGA    0.05  3.00000   
48                49    MUR-ADO_LWAL-DNO_H2  SA(0.3)    0.05  3.01009   
49                50     MUR-ST_LWAL-DNO_H1      PGA    0.05  3.00000   
50                51     MUR-ST_LWAL-DNO_H2  SA(0.3)    0.05  3.01009   

       lrMin     lrMax  
0   0.000000  0.944437  
1   0.000000  0.944437  
2   0.000000  0.921155  
3   0.000000  1.000000  
4   0.000000  0.998087  
5   0.000001  0.995247  
6   0.000013  0.990365  
7   0.0

### Vulnerability

In [72]:
vulnerabilities = pd.read_csv("./gem/model_data/GMO/vulnerability.csv")
vulnerabilities

vulnerability_id  intensity_bin_index  damage_bin_index  prob
0                    1                    1                 1     1
1                    1                    2                10     1
2                    1                    3                33     1
3                    1                    4                46     1
4                    1                    5                53     1
5                    1                    6                58     1
6                    1                    7                61     1
7                    1                    8                64     1
8                    1                    9                66     1
9                    1                   10                68     1
10                   1                   11                69     1
11                   1                   12                70     1
12                   1                   13                72     1
13                   1                   14                73     1
14                   1                   15                74     1
15                   1                   16                75     1
16                   1                   17                76     1
17                   1                   18                77     1
18                   1                   19                78     1
19                   1                   20                80     1
20                   1                   21                81     1
21                   1                   22                83     1
22                   1                   23                84     1
23                   1                   24                86     1
24                   1                   25                88     1
25                   1                   26                89     1
26                   1                   27                91     1
27                   1                   28                93     1
28                   1                   29                94     1
29                   1                   30                96     1
...                ...                  ...               ...   ...
5298                51                  180               166     1
5299                51                  181               166     1
5300                51                  182               166     1
5301                51                  183               166     1
5302                51                  184               166     1
5303                51                  185               166     1
5304                51                  186               166     1
5305                51                  187               166     1
5306                51                  188               166     1
5307                51                  189               166     1
5308                51                  190               166     1
5309                51                  191               166     1
5310                51                  192               166     1
5311                51                  193               166     1
5312                51                  194               166     1
5313                51                  195               166     1
5314                51                  196               166     1
5315                51                  197               166     1
5316                51                  198               166     1
5317                51                  199               166     1
5318                51                  200               166     1
5319                51                  201               166     1
5320                51                  202               166     1
5321                51                  203               166     1
5322                51                  204               166     1
5323                51                  205               166     1
5324                51                  206               166 

In [81]:
vulnerability_id = 1

def joy(category, data, scale=1):
    return list(zip([category]*len(data), scale*data))

num_intensity_bins = len(intensity_bin_dictionary.bin_index)
num_damage_bins = len(damage_bin_dictionary.bin_index)

z = linspace(0, 100, num_damage_bins+1)
x = np.delete(z, num_damage_bins)
x = np.insert(x, 0, -1.5)


intensity_range = list([str(i) for i in intensity_bin_dictionary.bin_index])

p = figure(y_range=intensity_range, plot_width=900, x_range=(0, 105), toolbar_location=None)


#data = vulnerabilities[vulnerabilities.vulnerability_id==vulnerability_id]


#for i, intensity_bin_id in enumerate(reversed(intensity_range)):        
#    all_damage_bins=pd.DataFrame({"damage_bin_index": list(range(0,num_damage_bins+1))})
#    d = all_damage_bins.merge(data[data.intensity_bin_index==int(intensity_bin_id)], on="damage_bin_index", how="outer")
#    d = d.fillna(0)
#           
#    y = joy(intensity_bin_id, d.prob, 10)
#
#    top =[]
#    for i in range(len(y)):
#        top.append((y[i][1])+int(y[i][0])-0.5)
#    bottom = []
#    for i in range(len(y)):
#        bottom.append(int(y[i][0])-0.5)
# 
#    p.quad(left=x, right=z, top=top, bottom=bottom, alpha = 0.6)
#
#
#p.outline_line_color = "black"
#p.background_fill_color = "#efefef"
#
#p.xaxis.ticker = FixedTicker(ticks=list(range(0, 105, 10)))
#p.xaxis.formatter = PrintfTickFormatter(format="%d%%")
#
#p.ygrid.grid_line_color = None
#p.xgrid.grid_line_color = "#dddddd"
#p.xgrid.ticker = p.xaxis[0].ticker
#
#p.axis.minor_tick_line_color = None
#p.axis.major_tick_line_color = None
#p.axis.axis_line_color = None
#
#p.xaxis.axis_label = 'Damage'
#p.yaxis.axis_label = 'Hazard'
#
#p.y_range.range_padding = 0.12
#show(p)

vulnerability_id  intensity_bin_index  damage_bin_index  prob
0                   1                    1                 1     1
1                   1                    2                10     1
2                   1                    3                33     1
3                   1                    4                46     1
4                   1                    5                53     1
5                   1                    6                58     1
6                   1                    7                61     1
7                   1                    8                64     1
8                   1                    9                66     1
9                   1                   10                68     1
10                  1                   11                69     1
11                  1                   12                70     1
12                  1                   13                72     1
13                  1                   14                73     1
14                  1                   15                74     1
15                  1                   16                75     1
16                  1                   17                76     1
17                  1                   18                77     1
18                  1                   19                78     1
19                  1                   20                80     1
20                  1                   21                81     1
21                  1                   22                83     1
22                  1                   23                84     1
23                  1                   24                86     1
24                  1                   25                88     1
25                  1                   26                89     1
26                  1                   27                91     1
27                  1                   28                93     1
28                  1                   29                94     1
29                  1                   30                96     1
..                ...                  ...               ...   ...
74                  1                   75               151     1
75                  1                   76               151     1
76                  1                   77               152     1
77                  1                   78               152     1
78                  1                   79               153     1
79                  1                   80               153     1
80                  1                   81               154     1
81                  1                   82               154     1
82                  1                   83               155     1
83                  1                   84               155     1
84                  1                   85               155     1
85                  1                   86               156     1
86                  1                   87               156     1
87                  1                   88               157     1
88                  1                   89               157     1
89                  1                   90               157     1
90                  1                   91               158     1
91                  1                   92               158     1
92                  1                   93               158     1
93                  1                   94               158     1
94                  1                   95               159     1
95                  1                   96               159     1
96                  1                   97               159     1
97                  1                   98               160     1
98                  1                   99               160     1
99                  1                  100               160     1
100                 1                  101               160     1
101                 1                  102          

### Occurrence file

In [83]:
occurrences = pd.read_csv("gem/model_data/GMO/occurrence.csv")
occurrences

event_id  period_no  occ_year  occ_month  occ_day
0          699          1         1          1       29
1         1786          2         2          7       19
2         2395          3         3         10       28
3         1009          4         4          3        6
4         3820          4         4         10       24
5         5492          5         5          9       20
6         4071          6         6          3       11
7         3169          7         7         10       10
8          878          8         8         10       10
9         2903          8         8         11        6
10        2587          9         9          4        6
11        4494          9         9          5       19
12         449         10        10         12       29
13        1416         11        11          2       20
14         931         11        11          5       26
15        1840         12        12         11        9
16        2385         13        13          9       20
17        4017         13        13         12       22
18        3824         14        14          1       15
19        5482         14        14          3       18
20        1611         15        15         12       19
21        3077         16        16         11        5
22         967         17        17          5        2
23        3426         17        17         11       15
24          61         18        18         11        7
25        5607         19        19          6       28
26        2970         20        20          4       11
27        3950         21        21          1        2
28        4541         21        21          5        4
29        5234         21        21          9       24
...        ...        ...       ...        ...      ...
5588      2008       4966      4966          9       20
5589      5084       4967      4967          4        5
5590      4283       4968      4968          6       10
5591      2646       4969      4969          3        9
5592      2955       4970      4970          8        4
5593      1176       4971      4971          8       24
5594      1394       4977      4977         11       16
5595      2950       4978      4978         12        3
5596      4446       4979      4979         12       17
5597      1586       4982      4982          7       19
5598       782       4982      4982          9        7
5599       281       4983      4983          5       28
5600      5070       4983      4983         11       12
5601      4845       4986      4986         12       20
5602      1501       4987      4987          4       25
5603      3974       4988      4988          7       10
5604       882       4989      4989          7       17
5605      1305       4989      4989         10        9
5606      2819       4990      4990          3        3
5607      5352       4991      4991          9        3
5608      4163       4991      4991         10       12
5609      2900       4992      4992          9        8
5610      4964       4992      4992         10       15
5611       733       4994      4994          7       28
5612      5617       4995      4995          1       29
5613       939       4996      4996          2       26
5614      4600       4996      4996          3        3
5615      5432       4999      4999          2        1
5616       222       4999      4999          8       19
5617      2379       5000      5000          8        1

[5618 rows x 5 columns]

## Model execution

To run the model we need some test exxposure data. Lets have a look at an example Location and Account file. 

In [84]:
test_locations = pd.read_csv('./gem/tests/data/dom-rep-146-oed-location.csv')
test_locations.head()


PortNumber  AccNumber  LocNumber    GeogName1      AreaName1  Latitude  \
0           1        146      10527  Pedro Brand  Santo Domingo  18.64788   
1           1        146      10526  Pedro Brand  Santo Domingo  18.64788   
2           1        146      10525  Pedro Brand  Santo Domingo  18.64788   
3           1        146      10524  Pedro Brand  Santo Domingo  18.64788   
4           1        146      10523  Pedro Brand  Santo Domingo  18.64788   

   Longitude CountryCode ConstructionCode  OccupancyCode  YearBuilt  \
0  -70.09339          DR             5050           1050       1900   
1  -70.09339          DR             5050           1050       1900   
2  -70.09339          DR             5050           1050       1900   
3  -70.09339          DR             5050           1050       1900   
4  -70.09339          DR             5050           1050       1900   

   YearUpgraded  NumberOfStoreys  NumberOfBuildings LocPerilsCovered  \
0          1900                1                695              QEQ   
1          1900                2                139              QEQ   
2          1900                2                266              QEQ   
3          1900                1                524              QEQ   
4          1900                1                197              QEQ   

   BuildingTIV  
0   12009600.0  
1    3602880.0  
2    6894720.0  
3    9054720.0  
4    3404160.0

To run the model, we also need to define some analysis settings. Lets have a look at an example settings file.

In [85]:
with open('gem/tests/analysis_settings.json', 'r') as myfile:
    analysis_settings=json.loads(myfile.read().replace('\n', ''))
print(json.dumps(analysis_settings, indent=True))

{
 "analysis_settings": {
  "gul_threshold": 0,
  "ri_summaries": [
   {
    "leccalc": {
     "outputs": {
      "full_uncertainty_aep": true,
      "full_uncertainty_oep": true
     },
     "return_period_file": true
    },
    "id": 1,
    "aalcalc": true,
    "eltcalc": true,
    "lec_output": true
   }
  ],
  "number_of_samples": 10,
  "ri_output": true,
  "model_version_id": "GMO",
  "il_summaries": [
   {
    "leccalc": {
     "outputs": {
      "full_uncertainty_aep": true,
      "full_uncertainty_oep": true
     },
     "return_period_file": true
    },
    "id": 1,
    "aalcalc": true,
    "eltcalc": true,
    "lec_output": true
   }
  ],
  "model_settings": {},
  "il_output": true,
  "gul_summaries": [
   {
    "leccalc": {
     "outputs": {
      "full_uncertainty_aep": true,
      "full_uncertainty_oep": true
     },
     "return_period_file": true
    },
    "id": 1,
    "aalcalc": true,
    "eltcalc": true,
    "lec_output": true
   }
  ],
  "source_tag": "GEM",
  "gul_o

In [ ]:
! damagebintobin < ./model_data/MEEQ/damage_bin_dict.csv > ./model_data/MEEQ/damage_bin_dict.bin 
! evetobin < ./model_data/MEEQ/events_subset.csv > ./model_data/MEEQ/events.bin
! vulnerabilitytobin -d 52 < ./model_data/MEEQ/vulnerability_subset.csv > ./model_data/MEEQ/vulnerability.bin
! footprinttobin -i 30 < ./model_data/MEEQ/footprint_subset.csv
! occurrencetobin -P 10000 -D < ./model_data/MEEQ/occurrence.csv > ./model_data/MEEQ/occurrence.bin
! returnperiodtobin < ./model_data/MEEQ/returnperiods.csv  > ./model_data/MEEQ/returnperiods.bin

In [86]:
! rm -rf /tmp/analysis_test
! oasislmf model run -C gem/oasislmf.json -r /tmp/analysis_test


Processing arguments for model run
  0%|                                                     | 0/2 [00:00<?, ?it/s]
Processing arguments

Generating Oasis files (GUL=True, IL=True, RI=False)
STARTED: oasislmf.manager.__init__
COMPLETED: oasislmf.manager.__init__ in 0.0s
STARTED: oasislmf.manager.generate_oasis_files

Traceback (most recent call last):
  File "/home/pinkerton/git/Workshop2019/venv/bin/oasislmf", line 7, in <module>
    sys.exit(RootCmd().run())
  File "/home/pinkerton/git/Workshop2019/venv/lib/python3.5/site-packages/oasislmf/cli/root.py", line 40, in run
    return super(OasisBaseCommand, self).run(args=args)
  File "/home/pinkerton/git/Workshop2019/venv/lib/python3.5/site-packages/argparsetree/cmd.py", line 159, in run
    return cmd_cls(sub_command_name).run(args)
  File "/home/pinkerton/git/Workshop2019/venv/lib/python3.5/site-packages/argparsetree/cmd.py", line 159, in run
    return cmd_cls(sub_command_name).run(args)
  File "/home/pinkerton/git/Workshop2019/venv

In [ ]:
analysis_directory = "/tmp/analysis_test"

all_dictionary = pd.read_csv(os.path.join(analysis_directory, "tmp", "canexp.csv"))
all_dictionary.head()

In [ ]:
! more /tmp/analysis_test/output/gul_S1_aalcalc.csv

In [ ]:
from bokeh.io import show, output_file
from bokeh.models import ColumnDataSource, FactorRange
from bokeh.plotting import figure
from bokeh.transform import factor_cmap

analysis_directory = "/tmp/analysis_test"
gul_aep = pd.read_csv(os.path.join(analysis_directory, "output", "gul_S1_leccalc_full_uncertainty_aep.csv"))
gul_oep = pd.read_csv(os.path.join(analysis_directory, "output", "gul_S1_leccalc_full_uncertainty_oep.csv"))
eps = pd.merge(gul_oep, gul_aep, on=["summary_id", "return_period"], suffixes=["_oep", "_aep"])
eps = eps.sort_values(by="return_period", ascending=True)
return_periods = eps.return_period
lec_types = ['OEP', 'AEP']
data = {'Return periods' : return_periods,
       'OEP': eps.loss_oep,
       'AEP': eps.loss_aep}
palette = ["#c9d9d3", "#718dbf"]
x = [ (str(return_period), lec_type) for return_period in return_periods for lec_type in lec_types ]
counts = sum(zip(data['OEP'], data['AEP']), ())
source = ColumnDataSource(data=dict(x=x, counts=counts))
p = figure(x_range=FactorRange(*x), plot_height=350, title="EP by return period",
          toolbar_location=None, tools="")
p.vbar(x='x', top='counts', width=0.9, source=source, line_color="white",
      fill_color=factor_cmap('x', palette=palette, factors=lec_types, start=1, end=2))
p.y_range.start = 0
p.x_range.range_padding = 0.1
p.xaxis.major_label_orientation = 1
p.xgrid.grid_line_color = None
show(p)

## Un-modelled exposure data

Some accounts may be missing the necessary data for a successful model run. The key lookup returns the details of the problematic exposure data in a separate oasiskeys-errors file with the error message.

In [ ]:
analysis_directory = "/tmp/analysis_test"

all_dictionary = pd.read_csv(os.path.join(analysis_directory, "tmp", "canexp.csv"))
all_dictionary.head()

In [ ]:
success_dictionary = pd.read_csv(os.path.join(analysis_directory, "tmp", "oasiskeys.csv"))
success_dictionary.head()

In [ ]:
failure_dictionary = pd.read_csv(os.path.join(analysis_directory, "tmp", "oasiskeyserrors.csv"))
failure_dictionary.head()

In [ ]:
m = folium.Map(location=[	33.85, 35.50], zoom_start=12, tiles='cartodbpositron')

#Red for errors, blue for success

for i, row in failure_dictionary.iterrows():
    loc = failure_dictionary.at[i, 'LocID'] - 1
    lat = all_dictionary.loc[loc, 'LATITUDE']
    lon = all_dictionary.loc[loc, 'LONGITUDE']
    folium.CircleMarker(
        location=[lat, lon], radius=1, color='red').add_to(m)

for i, row in success_dictionary.iterrows():
    loc = success_dictionary.at[i, 'LocID'] - 1
    lat = all_dictionary.loc[loc, 'LATITUDE']
    lon = all_dictionary.loc[loc, 'LONGITUDE']
    folium.CircleMarker(
        location=[lat, lon], radius=1).add_to(m)
m.fit_bounds(m.get_bounds())
m